# Set up imports

In [1]:
# setting up our imports
import re, string, unicodedata
import numpy as np
import pandas as pd
from pprint import pprint
import nltk
from nltk.corpus import stopwords
nltk.download('stopwords')
stop_words = stopwords.words('english')

# Gensim
import gensim
import gensim.corpora as corpora
from gensim.utils import simple_preprocess
from gensim.models import CoherenceModel
from gensim.models import LdaModel, LdaMulticore
import gensim.downloader as api
from gensim.models import LsiModel
from gensim.models import ldaseqmodel
from gensim.corpora import Dictionary, bleicorpus
from gensim.matutils import hellinger

nltk.download('wordnet')
from nltk.stem.porter import PorterStemmer
from nltk.stem.wordnet import WordNetLemmatizer
#from bs4 import BeautifulSoup
#from nltk import word_tokenize, sent_tokenize

# Plotting tools 
import pyLDAvis
import pyLDAvis.gensim  # don't skip this
import matplotlib.pyplot as plt
# %matplotlib inline

# Enable logging for gensim - optional
#import logging
#logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.ERROR)
#logging.root.setLevel(level=logging.INFO)
#import warnings
#warnings.filterwarnings("ignore",category=DeprecationWarning)

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\Kornelius\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\utils.py:1197: UserWarning: detected Windows; aliasing chunkize to chunkize_serial
  warnings.warn("detected Windows; aliasing chunkize to chunkize_serial")
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\Kornelius\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


# load dataset

In [2]:
# Load dataset
df = pd.read_excel('C:/Users/Kornelius/Desktop/Data 2/ecbpr/Warin_Sanger_ECB.xlsx') 
df.head()


C:\Users\Kornelius\Anaconda3\lib\site-packages\defusedxml\ElementTree.py:68: DeprecationWarning: The html argument of XMLParser() is deprecated
  _XMLParser.__init__(self, html, target, encoding)
C:\Users\Kornelius\Anaconda3\lib\site-packages\defusedxml\ElementTree.py:68: DeprecationWarning: The html argument of XMLParser() is deprecated
  _XMLParser.__init__(self, html, target, encoding)
C:\Users\Kornelius\Anaconda3\lib\site-packages\defusedxml\ElementTree.py:68: DeprecationWarning: The html argument of XMLParser() is deprecated
  _XMLParser.__init__(self, html, target, encoding)
C:\Users\Kornelius\Anaconda3\lib\site-packages\defusedxml\ElementTree.py:68: DeprecationWarning: The html argument of XMLParser() is deprecated
  _XMLParser.__init__(self, html, target, encoding)
C:\Users\Kornelius\Anaconda3\lib\site-packages\defusedxml\ElementTree.py:68: DeprecationWarning: The html argument of XMLParser() is deprecated
  _XMLParser.__init__(self, html, target, encoding)
C:\Users\Kornelius\A

Date                                              Press  \
0  1998  Ladies and gentlemen, in line with our stated ...   
1  1998  Ladies and gentlemen, as in previous months, t...   
2  1998  Ladies and gentlemen, the Vice-President and I...   
3  1998  Ladies and gentlemen, the Vice-President and I...   
4  1999  Ladies and gentlemen, the Vice-President and I...   

                                                  qa  
0  We have no indications based on the most recen...  
1  The answer to the first question is that it is...  
2  We simply felt that the announcement of a rang...  
3  No, that is not a signal that it is supposed t...  
4  The main problems have not been technical ones...

In [3]:
# sort by year
df = df.sort_values(by=['Date'])
df

Date                                              Press  \
0    1998  Ladies and gentlemen, in line with our stated ...   
1    1998  Ladies and gentlemen, as in previous months, t...   
2    1998  Ladies and gentlemen, the Vice-President and I...   
3    1998  Ladies and gentlemen, the Vice-President and I...   
14   1999  Ladies and gentlemen, the Vice-President and I...   
13   1999  Ladies and gentlemen,\nthe Vice-President and ...   
12   1999  Ladies and gentlemen,\nthe Vice-President and ...   
11   1999  Ladies and gentlemen, the Vice-President and I...   
9    1999  Ladies and gentlemen, the Vice-President and I...   
10   1999  Ladies and gentlemen, the Vice-President and I...   
7    1999  Ladies and gentlemen, the Vice-President and I...   
6    1999  Ladies and gentlemen, the Vice-President and I...   
5    1999  Ladies and gentlemen, the Vice-President and I...   
4    1999  Ladies and gentlemen, the Vice-President and I...   
8    1999  Ladies and gentlemen, the Vice-President and I...   
22   2000  Ladies and gentlemen, the Vice-President and I...   
27   2000  Ladies and gentlemen, the Vice-President and I...   
25   2000  Ladies and gentlemen,\nToday, the Governing Co...   
24   2000  Ladies and gentlemen, the Vice-President and I...   
23   2000  Ladies and gentlemen, the Vice-President and I...   
21   2000  Ladies and gentlemen, the Vice-President and I...   
26   2000  Ladies and gentlemen, the Vice-President and I...   
19   2000  Ladies and gentlemen, the Vice-President and I...   
18   2000  Ladies and gentlemen, today, the Governing Cou...   
17   2000  Ladies and gentlemen, the Vice-President and I...   
16   2000  Ladies and gentlemen,\nthe Vice-President and ...   
20   2000  Ladies and gentlemen, the Vice-President and I...   
15   2000  Ladies and gentlemen, the Vice-President and I...   
36   2001  Ladies and gentlemen, the Vice-President and I...   
35   2001  Ladies and gentlemen, the Vice-President and I...   
..    ...                                                ...   
165  2013  Ladies and gentlemen, the Vice-President and I...   
170  2013  Ladies and gentlemen, the Vice-President and I...   
188  2014  Ladies and gentlemen, the Vice-President and I...   
186  2014  Ladies and gentlemen, the Vice-President and I...   
185  2014  Ladies and gentlemen, the Vice-President and I...   
184  2014  Ladies and gentlemen, the Vice-President and I...   
183  2014  Ladies and gentlemen, the Vice-President and I...   
187  2014  Ladies and gentlemen, the Vice-President and I...   
181  2014  Ladies and gentlemen, the Vice-President and I...   
180  2014  Ladies and gentlemen, the Vice-President and I...   
179  2014  Ladies and gentlemen, the Vice-President and I...   
178  2014  Ladies and gentlemen, the Vice-President and I...   
177  2014  Ladies and gentlemen, the Vice-President and I...   
182  2014  Ladies and gentlemen, the Vice-President and I...   
196  2015  Ladies and gentlemen, the Vice-President and I...   
195  2015  Ladies and gentlemen, the Vice-President and I...   
194  2015  Ladies and gentlemen, the Vice-President and I...   
193  2015  Ladies and gentlemen, the Vice-President and I...   
191  2015  Ladies and gentlemen, the Vice-President and I...   
190  2015  Ladies and gentlemen, the Vice-President and I...   
189  2015  Ladies and gentlemen, the Vice-President and I...   
192  2015  Ladies and gentlemen, the Vice-President and I...   
203  2016  Ladies and gentlemen, the Vice-President and I...   
197  2016  Ladies and gentlemen, first of all let me wish...   
198  2016  Ladies and gentlemen, the Vice-President and I...   
199  2016  Ladies and gentlemen, the Vice-President and I...   
200  2016  Ladies and gentlemen, the Vice-President and I...   
201  2016  Ladies and gentlemen, the Vice-President and I...   
202  2016  Ladies and gentlemen, the Vice-President and I...   
204  2016  Ladies and gentlemen, the Vice-President and I...   

                                    

In [4]:
# sort by year
data = df['qa']

In [5]:
from nltk.corpus import stopwords 
from nltk.stem.wordnet import WordNetLemmatizer
import string
stop = set(stopwords.words('english'))
exclude = set(string.punctuation) 
lemma = WordNetLemmatizer()
def clean(data):
    stop_free = " ".join([i for i in data.lower().split() if i not in stop])
    punc_free = ''.join(ch for ch in stop_free if ch not in exclude)
    normalized = " ".join(lemma.lemmatize(word) for word in punc_free.split())
    return normalized

data = [clean(data).split() for data in data]  

In [6]:
# remove characters and numbers
def sent_to_words(sentences):
    for sentence in sentences:
        yield(gensim.utils.simple_preprocess(str(sentence), deacc=True))  # deacc=True removes punctuations

data_words = list(sent_to_words(data))


In [28]:
data_words

[['indication',
  'based',
  'recent',
  'data',
  'tendency',
  'deflation',
  'present',
  'would',
  'like',
  'point',
  'definition',
  'price',
  'stability',
  'purpose',
  'talk',
  'increase',
  'price',
  'per',
  'cent',
  'time',
  'bias',
  'direction',
  'price',
  'stability',
  'zero',
  'increase',
  'inflation',
  'accept',
  'deflation',
  'aim',
  'show',
  'formulation',
  'monetary',
  'policy',
  'easy',
  'current',
  'circumstance',
  'well',
  'thats',
  'statement',
  'fact',
  'would',
  'say',
  'well',
  'tried',
  'emphasise',
  'talk',
  'internationally',
  'particularly',
  'annual',
  'meeting',
  'washington',
  'crisis',
  'hand',
  'mind',
  'exaggerated',
  'somewhat',
  'overdone',
  'indicated',
  'europe',
  'united',
  'state',
  'still',
  'situation',
  'relatively',
  'robust',
  'economic',
  'development',
  'sign',
  'may',
  'slowdown',
  'certainly',
  'inclined',
  'talk',
  'term',
  'crisis',
  'area',
  'now',
  'come',
  'question

In [7]:
data = data_words
# Create Dictionary
id2word = corpora.Dictionary(data)
print((id2word))

Dictionary(8371 unique tokens: ['absence', 'accept', 'achieve', 'activity', 'add']...)


In [8]:
# filter words that occur in more than 90% of documents
id2word.filter_extremes(no_above = 0.980)
print(id2word)

Dictionary(3462 unique tokens: ['absence', 'accept', 'achieve', 'activity', 'add']...)


In [9]:
# Create Corpus
texts = data
# Term Document Frequency and creating corpus
corpus = [id2word.doc2bow(text) for text in texts]

In [10]:
from gensim.models import ldaseqmodel
import numpy
from gensim.matutils import hellinger

In [11]:
time_slice = [4 , 11, 13, 9, 11, 11, 11, 11, 12, 12, 12, 12, 12, 12, 12, 12, 12, 8, 8]



In [12]:
#ldaseq = ldaseqmodel.LdaSeqModel(corpus=corpus, id2word=id2word, time_slice=time_slice, num_topics=5)

ldaseq = ldaseqmodel.LdaSeqModel(corpus=corpus , id2word=id2word , num_topics=10, time_slice=time_slice)

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

...

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

In [13]:
#ldaseq.print_topics(time=0) # at timeslice 1, those are the topics, word probability to the right 

In [14]:
ldaseq.print_topic_times(topic=0) # evolution of 1st topic through all timeslices

[[('development', 0.008372655665415825),
  ('bank', 0.008125667935438927),
  ('central', 0.008066021797608496),
  ('exchange', 0.008048501043163996),
  ('market', 0.007180145592830228),
  ('price', 0.006728713408846352),
  ('today', 0.006424934019031357),
  ('area', 0.006209176433056671),
  ('may', 0.0061001322458382485),
  ('year', 0.005878292280813245),
  ('growth', 0.0057005518496151),
  ('country', 0.005610659520940115),
  ('way', 0.005488325832854295),
  ('last', 0.005391015856418676),
  ('think', 0.005271055426645648),
  ('european', 0.0048166776231765044),
  ('course', 0.0047975018235446995),
  ('so', 0.004787259860418416),
  ('still', 0.00476717815138144),
  ('future', 0.004724728705999272)],
 [('development', 0.008601515369863142),
  ('exchange', 0.008145806063785255),
  ('bank', 0.007893132516634049),
  ('central', 0.00773893685658793),
  ('market', 0.007167275864813164),
  ('price', 0.0066709069436058),
  ('today', 0.006590932711314785),
  ('area', 0.00617088217964278),
  ('

In [15]:
ldaseq.print_topic_times(topic=1) 

[[('council', 0.021817329950440917),
  ('ecb', 0.014088285034205207),
  ('european', 0.013681055901199795),
  ('treaty', 0.013260776454979719),
  ('governing', 0.012073096003502343),
  ('meeting', 0.01164055346379488),
  ('answer', 0.008315738011058177),
  ('think', 0.007976930440730619),
  ('proposal', 0.007910426745347565),
  ('decision', 0.007869618467459828),
  ('cannot', 0.007480101441254859),
  ('already', 0.007126530879986456),
  ('comment', 0.0070234392460133835),
  ('year', 0.006726689390516525),
  ('opinion', 0.006707480637426593),
  ('president', 0.006690688451093616),
  ('growth', 0.006648426662601821),
  ('minister', 0.0061930796333092295),
  ('government', 0.0058164875145521044),
  ('course', 0.005746740806848071)],
 [('council', 0.021431355854253067),
  ('ecb', 0.014144060569346643),
  ('european', 0.013665834714294141),
  ('treaty', 0.013119604118462634),
  ('governing', 0.012084489791571621),
  ('meeting', 0.0114772064771278),
  ('answer', 0.0081515764126932),
  ('thin

In [16]:
ldaseq.print_topic_times(topic=2) 

[[('market', 0.018532094099957673),
  ('price', 0.009791404510748992),
  ('risk', 0.009266325510204558),
  ('regard', 0.008886706676764927),
  ('stability', 0.008097609297072665),
  ('economy', 0.007990622986278891),
  ('governing', 0.007093784619078889),
  ('level', 0.007066430970957066),
  ('council', 0.006987681481764256),
  ('number', 0.006895498006446666),
  ('see', 0.005917317454307898),
  ('bank', 0.005843849733624466),
  ('inflation', 0.005842602550522589),
  ('important', 0.005757467485434204),
  ('situation', 0.00548592092870335),
  ('expectation', 0.005352614824262828),
  ('financial', 0.005268888117995719),
  ('again', 0.0048337935980784135),
  ('continue', 0.004571778137700048),
  ('growth', 0.004421668304050327)],
 [('market', 0.018579772038459386),
  ('price', 0.009811475366916856),
  ('risk', 0.009286566242000168),
  ('regard', 0.008903810564871896),
  ('stability', 0.008113131337413858),
  ('economy', 0.008006324599381602),
  ('governing', 0.007106562375976408),
  ('le

In [17]:
ldaseq.print_topic_times(topic=3) 

[[('growth', 0.010853023898615068),
  ('year', 0.01061239378299867),
  ('inflation', 0.010481276208881557),
  ('price', 0.010067358670872372),
  ('development', 0.007996183496051721),
  ('stability', 0.007798635466843849),
  ('economic', 0.006810068856333499),
  ('area', 0.006666531234975547),
  ('course', 0.006337518479898871),
  ('believe', 0.005811584688862178),
  ('interest', 0.005593439151494617),
  ('today', 0.005383435149095095),
  ('statement', 0.005381062800173052),
  ('level', 0.00526766184433886),
  ('month', 0.005185590010946296),
  ('see', 0.0051850533303581135),
  ('impact', 0.005116514416750754),
  ('take', 0.005058458724062884),
  ('factor', 0.004779901010025797),
  ('come', 0.004733092707016633)],
 [('growth', 0.01103390236894337),
  ('year', 0.010805639630903693),
  ('inflation', 0.010599036789590496),
  ('price', 0.009923074207004796),
  ('development', 0.00799113278554949),
  ('stability', 0.007599372618065662),
  ('economic', 0.006842970269231408),
  ('area', 0.006

In [18]:
ldaseq.print_topic_times(topic=4) 

[[('government', 0.012404312678514872),
  ('country', 0.012372577846170137),
  ('stability', 0.01050345520945912),
  ('decision', 0.010424014115551614),
  ('regard', 0.009466710406777637),
  ('council', 0.007949243850773786),
  ('area', 0.007536906633941822),
  ('governing', 0.007309046916755856),
  ('year', 0.006372398547037589),
  ('market', 0.006304095222776409),
  ('important', 0.00630231933567744),
  ('growth', 0.006002078265058897),
  ('message', 0.0057141366364283405),
  ('appropriate', 0.005692511049483576),
  ('second', 0.005678511204766382),
  ('measure', 0.005646140040501334),
  ('economy', 0.0053450923205932655),
  ('see', 0.0052849690255942945),
  ('state', 0.004944843132354483),
  ('know', 0.004939044092834627)],
 [('government', 0.012435624663452933),
  ('country', 0.012393727818646406),
  ('stability', 0.010510357514725828),
  ('decision', 0.010449280208786249),
  ('regard', 0.009479986134494424),
  ('council', 0.0079643643791557),
  ('area', 0.007551452980240811),
  ('

In [23]:
ldaseq.print_topic_times(topic=5) 

[[('think', 0.011460441655216523),
  ('country', 0.009710215263516389),
  ('bank', 0.00824234986636939),
  ('ecb', 0.007465321629899219),
  ('second', 0.007044728954024829),
  ('market', 0.006151924289187435),
  ('price', 0.006064447237003725),
  ('area', 0.005992039140950088),
  ('risk', 0.0058693404681356654),
  ('see', 0.005706679285127716),
  ('point', 0.0054574251068705976),
  ('so', 0.005330305863840706),
  ('fiscal', 0.004946658127708839),
  ('actually', 0.004665788455075273),
  ('year', 0.004289091509494905),
  ('credit', 0.004067951427016523),
  ('certainly', 0.003988655955279677),
  ('thing', 0.003983219707401726),
  ('way', 0.003892136717024311),
  ('government', 0.003843435241252331)],
 [('think', 0.011494244129062565),
  ('country', 0.009734885809634608),
  ('bank', 0.008242823666379535),
  ('ecb', 0.0074805854447808845),
  ('second', 0.0070599305614254815),
  ('market', 0.006162559527483378),
  ('price', 0.006071681430089018),
  ('area', 0.006010102754208272),
  ('risk', 

In [24]:
ldaseq.print_topic_times(topic=6) 

[[('inflation', 0.03312393307901438),
  ('thats', 0.028373295018217875),
  ('expectation', 0.024300689108109726),
  ('purchase', 0.020302100831659273),
  ('condition', 0.018001108411131322),
  ('weve', 0.017255281823005307),
  ('programme', 0.016537603280264473),
  ('governing', 0.016505953646614016),
  ('instrument', 0.015794095187158255),
  ('council', 0.013588712541205698),
  ('debt', 0.013506534535355644),
  ('discussed', 0.013062853379565127),
  ('growth', 0.012849524180667284),
  ('answer', 0.012019766137802425),
  ('low', 0.011916616373239262),
  ('objective', 0.011684133021823022),
  ('committee', 0.011079136886346728),
  ('course', 0.010748134570197932),
  ('second', 0.010649975322594188),
  ('march', 0.010152463982643483)],
 [('inflation', 0.03317286999667923),
  ('thats', 0.028394943338914014),
  ('expectation', 0.024369231420726178),
  ('purchase', 0.02035281851369654),
  ('condition', 0.018011525698710833),
  ('weve', 0.01729360092188087),
  ('programme', 0.016572200029589

In [25]:
ldaseq.print_topic_times(topic=7) 

[[('decision', 0.026480101548771562),
  ('bank', 0.019049097572744183),
  ('liquidity', 0.015830340269954318),
  ('level', 0.013943133964192903),
  ('situation', 0.013272848184960908),
  ('taken', 0.013244364154278375),
  ('operation', 0.013139115102370683),
  ('measure', 0.01274704209279893),
  ('account', 0.011980108309507657),
  ('regard', 0.01107902594896169),
  ('market', 0.010993935429755582),
  ('see', 0.010620365262744123),
  ('basis', 0.01028011608399489),
  ('taking', 0.009721280690481773),
  ('today', 0.009507331583619187),
  ('point', 0.009093082085672145),
  ('appropriate', 0.008944862400685443),
  ('important', 0.008692907213614176),
  ('already', 0.008528804698758012),
  ('decided', 0.00819957435035206)],
 [('decision', 0.026632195502585672),
  ('bank', 0.01903390658959566),
  ('liquidity', 0.01587287183293383),
  ('level', 0.013942641210322864),
  ('taken', 0.013283499914966834),
  ('situation', 0.013233972837672216),
  ('operation', 0.013102165238394473),
  ('measure',

In [26]:
ldaseq.print_topic_times(topic=8) 

[[('price', 0.016217786132116517),
  ('stability', 0.011761142023992229),
  ('growth', 0.01023520106200333),
  ('regard', 0.009685400673018093),
  ('risk', 0.009656749316534593),
  ('see', 0.008321954670285977),
  ('level', 0.008317359522314372),
  ('area', 0.007331604461553135),
  ('market', 0.006298944911262522),
  ('increase', 0.006065611911535883),
  ('know', 0.006015881560314314),
  ('analysis', 0.005933210835549076),
  ('decision', 0.00589255235977633),
  ('information', 0.00580560448361884),
  ('important', 0.005673853866179699),
  ('year', 0.005564566034122569),
  ('economy', 0.0052317507419152144),
  ('inflation', 0.005209631206552906),
  ('term', 0.0049818639721737465),
  ('last', 0.004866690170461172)],
 [('price', 0.01620416349545081),
  ('stability', 0.011739868257049056),
  ('growth', 0.010186820850582092),
  ('risk', 0.009681846748772684),
  ('regard', 0.009641333628325047),
  ('level', 0.008363212663350137),
  ('see', 0.00833503777306333),
  ('area', 0.00733641255855646

In [27]:
ldaseq.print_topic_times(topic=9) 

[[('know', 0.009778661700867495),
  ('price', 0.009450341163243451),
  ('council', 0.008847208605135179),
  ('stability', 0.008800729657534593),
  ('growth', 0.00867350385475946),
  ('important', 0.00848439642965841),
  ('governing', 0.006749046557857168),
  ('economy', 0.006578344365840866),
  ('course', 0.00638304723607117),
  ('clear', 0.006258689231603831),
  ('level', 0.006041750707231856),
  ('market', 0.006037970449284826),
  ('inflation', 0.005624557708376366),
  ('europe', 0.005555622158128998),
  ('responsibility', 0.00550921572254789),
  ('again', 0.005487739621136715),
  ('regard', 0.005471164122653906),
  ('situation', 0.0052451972731839954),
  ('present', 0.005197954587517523),
  ('analysis', 0.005139427418302287)],
 [('know', 0.00981106933217872),
  ('price', 0.009468410870043183),
  ('council', 0.008858315278967953),
  ('stability', 0.008803489803064368),
  ('growth', 0.008692332670725531),
  ('important', 0.008494780158352856),
  ('governing', 0.006759487270017124),
  

In [19]:
        # to check Document - Topic proportions, use `doc-topics`
#doc = ldaseq.doc_topics(558) # check the 558th document in the corpuses topic distribution
#print (doc)
# this document is made up of different topics like this

In [20]:
    # make a graph by checking the topic proportions and putting them on a graph 
# same with coherence
# do hellingers distance between topics?

In [21]:
ldaseq.print_topic_times(1) # evolution of 2nd topic through all timeslices


[[('council', 0.021817329950440917),
  ('ecb', 0.014088285034205207),
  ('european', 0.013681055901199795),
  ('treaty', 0.013260776454979719),
  ('governing', 0.012073096003502343),
  ('meeting', 0.01164055346379488),
  ('answer', 0.008315738011058177),
  ('think', 0.007976930440730619),
  ('proposal', 0.007910426745347565),
  ('decision', 0.007869618467459828),
  ('cannot', 0.007480101441254859),
  ('already', 0.007126530879986456),
  ('comment', 0.0070234392460133835),
  ('year', 0.006726689390516525),
  ('opinion', 0.006707480637426593),
  ('president', 0.006690688451093616),
  ('growth', 0.006648426662601821),
  ('minister', 0.0061930796333092295),
  ('government', 0.0058164875145521044),
  ('course', 0.005746740806848071)],
 [('council', 0.021431355854253067),
  ('ecb', 0.014144060569346643),
  ('european', 0.013665834714294141),
  ('treaty', 0.013119604118462634),
  ('governing', 0.012084489791571621),
  ('meeting', 0.0114772064771278),
  ('answer', 0.0081515764126932),
  ('thin

In [22]:
from gensim.models.coherencemodel import CoherenceModel

# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=0)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass1", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV1", cm_DTM.get_coherence())


# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=1)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass1", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV1", cm_DTM.get_coherence())



topics_dtm = ldaseq.dtm_coherence(time=2)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass1", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV1", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=3)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass2", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV2", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=4)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass3", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV3", cm_DTM.get_coherence())




# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=5)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass4", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV4", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=6)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass5", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV5", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=7)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass6", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV6", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=8)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass7", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV7", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=9)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass8", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV8", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=10)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass9", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV9", cm_DTM.get_coherence())




# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=11)
# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass10", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV10", cm_DTM.get_coherence())


# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=12)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass11", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV11", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=13)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass12", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV12", cm_DTM.get_coherence())




# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=14)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass12", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV12", cm_DTM.get_coherence())


# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=15)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass12", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV12", cm_DTM.get_coherence())


# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=16)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass12", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV12", cm_DTM.get_coherence())

# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=17)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass12", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV12", cm_DTM.get_coherence())

# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=18)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass12", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV12", cm_DTM.get_coherence())

U_Mass1 -0.23291752551500075
CV1 0.3178642712099311
U_Mass1 -0.2308458362692208
CV1 0.3170191533814605
U_Mass1 -0.23175666000966616
CV1 0.31673377632322075
U_Mass2 -0.23378994006347206
CV2 0.31714882411536743
U_Mass3 -0.23619708228452505
CV3 0.3170088092629416
U_Mass4 -0.23343329902469007
CV4 0.31714882411536743
U_Mass5 -0.23273767097860593
CV5 0.31714882411536743
U_Mass6 -0.227158561476954
CV6 0.31545163769114315
U_Mass7 -0.24611074058907567
CV7 0.3149910214276602
U_Mass8 -0.2405924012275828
CV8 0.3143679240246942
U_Mass9 -0.24495179017781582
CV9 0.3177581026046242
U_Mass10 -0.2431301410969909
CV10 0.3186446644331632
U_Mass11 -0.23782475080878154
CV11 0.32149146188545585
U_Mass12 -0.2295478488862198
CV12 0.31965699456237445
U_Mass12 -0.22063225172586076
CV12 0.3164673507408582
U_Mass12 -0.22859401408011976
CV12 0.3172459828685541
U_Mass12 -0.23252392087753354
CV12 0.32032742372632816
U_Mass12 -0.23001714576695492
CV12 0.3230324892085783
U_Mass12 -0.22112746838115344
CV12 0.32157670570